<a href="https://colab.research.google.com/github/hwyum/deeplearning_nlp/blob/master/gluon_rnn_practice_kor.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
from google.colab import drive
drive.mount('/content/drive/')

Drive already mounted at /content/drive/; to attempt to forcibly remount, call drive.mount("/content/drive/", force_remount=True).


In [0]:
import os
os.chdir("drive/My Drive/Colab Notebooks/DLC_NLP lecture/")

# Gluon RNN 예제코드 (한글 - 어린왕자)

In [0]:
# ## data loading을 위한 패키지 설치
# !pip install gutenberg

In [0]:
# !git clone https://github.com/c-w/Gutenberg.git

In [0]:
# !apt-get install libdb++-dev
# !export BERKELEYDB_DIR=/usr
# !pip install -r ./Gutenberg/requirements-py3.pip

## package import

In [3]:
!apt-get update
!apt-get upgrade
!pip install mxnet-cu92mkl
!pip install gluonnlp matplotlib tqdm

Hit:1 http://archive.ubuntu.com/ubuntu bionic InRelease
Hit:2 http://ppa.launchpad.net/graphics-drivers/ppa/ubuntu bionic InRelease
Get:3 http://archive.ubuntu.com/ubuntu bionic-updates InRelease [88.7 kB]
Get:4 http://archive.ubuntu.com/ubuntu bionic-backports InRelease [74.6 kB]
Get:5 http://security.ubuntu.com/ubuntu bionic-security InRelease [83.2 kB]
Ign:6 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1710/x86_64  InRelease
Ign:7 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1604/x86_64  InRelease
Hit:8 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1710/x86_64  Release
Hit:9 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1604/x86_64  Release
Fetched 247 kB in 2s (153 kB/s)
Reading package lists... Done
Reading package lists... Done
Building dependency tree       
Reading state information... Done
Calculating upgrade... Done
The following packages have been kept back:
  libcudnn7 libnccl2
0 u

In [0]:
import pandas as pd
import numpy as np
# from konlpy.tag import Mecab
from mxnet.gluon import nn, rnn
from mxnet import gluon, autograd
import gluonnlp as nlp
from mxnet import nd 
import mxnet as mx
import multiprocessing as mp
from multiprocessing import Pool
import time
import itertools
from tqdm import tqdm, tqdm_notebook, trange
import re

mx.random.seed(1)
ctx = mx.gpu()

## 데이터 로딩

In [0]:
with codecs.open("./data/little_prince.txt", 'r', encoding='cp949') as f:
  prince = f.read()

In [13]:
print(prince[0:500])

여섯 살 적에 나는 "체험한 이야기"라는 제목의, 원시림에 관한 책에서 기막힌 그림 하나를 본 적이 있다. 맹수를 집어삼키고 있는 보아 구렁이 그림이었다. 위의 그림은 그것을 옮겨 그린 것이다.
 그 책에는 이렇게 씌어 있었다.
 "보아 구렁이는 먹이를 씹지도 않고 통째로 집어삼킨다.그리고는 꼼짝도 하지 못하고 여섯 달 동안 잠을 자면서 그것을 소화시킨다."
 나는 그래서 밀림 속에서의 모험에 대해 한참 생각해 보고 난 끝에 색연필을 가지고 내 나름대로 내 생애 첫번째 그림을 그려보았다. 나의 그림 제 1호였다. 그것은 이런 그림이었다.
 나는 그 걸작품을 어른들에게 보여 주면서내 그림이 무섭지 않느냐고 물었다.
 그들은 "모자가 뭐가 무섭다는 거니?" 하고 대답했다.
 내 그림은 모자를 그린 게 아니었다. 그것은 코끼리를 소화시키고 있는 보아 구렁이었다.
 그래서 나는 어른들이 알아볼 수 있도록 보아 구렁이의 속을 그렸다. 어른들은 언제나 설명을 해주어야만 한다. 나의


In [14]:
len(prince)

46748

In [15]:
print(prince[-100:])

 않으면 여러분은 그가누구인지 알아낼 수 있으리라.그러면 내게 친절을 베풀어 주길!내가 이처럼 마냥 슬퍼하도록 내버려두지 말고 그 애가 돌아왔다고 빨리 편지를 보내 주길......


In [24]:
prince.find('\n')

109

In [17]:
prince.find('\r')

108

In [0]:
# \n과 \r 을 ' '로 대체

prince = prince.replace('\n',' ')
prince = prince.replace('\r','')


## 데이터 전처리

### Numerical representations of characters


*   create numerical representations of characters
*   use one-hot representations
*   need to have definitive list of characters



In [26]:
# character 단위 생성을 위해 character set 정의

character_list = list(set(prince))
vocab_size = len(character_list)
print(character_list)
print('length of vocab: {}'.format(vocab_size))

['늬', '델', '닐', '紅', '흑', '쨌', '땀', '맥', '봐', '들', '퍼', '소', '향', '람', '돕', '릿', '경', '회', '꼼', '너', '이', '위', '개', '웬', '둔', '교', '결', '뚫', '짐', '몰', '렸', '쏘', '율', '틈', '미', '올', '的', '꼿', '야', '앉', '프', '5', '뀌', '잉', '님', '빤', '쭐', '쩔', '닷', '걷', '왼', '수', '칼', '렛', '발', '울', '에', '律', '괜', '힐', '면', '순', '늦', '북', '?', '뒤', '옥', '끼', '낙', '몇', '얄', '힌', '말', '밝', '엉', '멀', '쓱', '질', '듯', '小', '式', '당', '찾', '똑', '뵈', '되', '옛', '뜩', '버', '>', '넣', '구', '꺼', '털', '숙', '겠', '3', '빨', '클', '번', '엇', '를', '엄', '나', '짧', '隊', '맘', '덟', '낀', '때', '시', '간', '투', '신', '여', '엔', '잘', '충', '디', '엽', '왠', '왕', '7', '훗', '척', '혜', '귀', '혹', '使', '모', '선', '륭', '꺾', '춰', '짓', '록', '놀', '생', '루', '떳', '긍', '랐', '톱', '바', '애', '막', '찮', '팔', '"', '8', '네', '씌', '잰', '혁', '서', '차', '있', '詩', '닿', '겁', '옷', '겸', '늘', '째', '촉', '슨', '곧', '밤', '칠', '특', '보', '켰', '꽃', '뱃', '냥', '멩', '흐', '텅', '못', '윽', '휘', '잡', '튼', '먼', '런', '탁', '삐', '픔', '떨', '컨', '낌', '써', '술', '와', '텃', '행', '슷', '뭐', '슴', '사',

In [27]:
# 문장을 숫자 표현으로 바꾸기 위해 각 character별 index 부여

character_dict = {}
for e, char in enumerate(character_list):
  character_dict[char] = e
print(character_dict)

{'늬': 0, '델': 1, '닐': 2, '紅': 3, '흑': 4, '쨌': 5, '땀': 6, '맥': 7, '봐': 8, '들': 9, '퍼': 10, '소': 11, '향': 12, '람': 13, '돕': 14, '릿': 15, '경': 16, '회': 17, '꼼': 18, '너': 19, '이': 20, '위': 21, '개': 22, '웬': 23, '둔': 24, '교': 25, '결': 26, '뚫': 27, '짐': 28, '몰': 29, '렸': 30, '쏘': 31, '율': 32, '틈': 33, '미': 34, '올': 35, '的': 36, '꼿': 37, '야': 38, '앉': 39, '프': 40, '5': 41, '뀌': 42, '잉': 43, '님': 44, '빤': 45, '쭐': 46, '쩔': 47, '닷': 48, '걷': 49, '왼': 50, '수': 51, '칼': 52, '렛': 53, '발': 54, '울': 55, '에': 56, '律': 57, '괜': 58, '힐': 59, '면': 60, '순': 61, '늦': 62, '북': 63, '?': 64, '뒤': 65, '옥': 66, '끼': 67, '낙': 68, '몇': 69, '얄': 70, '힌': 71, '말': 72, '밝': 73, '엉': 74, '멀': 75, '쓱': 76, '질': 77, '듯': 78, '小': 79, '式': 80, '당': 81, '찾': 82, '똑': 83, '뵈': 84, '되': 85, '옛': 86, '뜩': 87, '버': 88, '>': 89, '넣': 90, '구': 91, '꺼': 92, '털': 93, '숙': 94, '겠': 95, '3': 96, '빨': 97, '클': 98, '번': 99, '엇': 100, '를': 101, '엄': 102, '나': 103, '짧': 104, '隊': 105, '맘': 106, '덟': 107, '낀': 108, '때': 109, '시': 110,

In [0]:
# character --> 숫자 표현으로 변경
prince_numerical = [character_dict[char] for char in prince]

In [30]:
# check format
print(len(prince_numerical))
print(prince_numerical[:20])

#convert back to text
print("".join([character_list[idx] for idx in prince_numerical[:50]]))

45772
[114, 679, 540, 308, 540, 749, 56, 540, 103, 726, 540, 148, 748, 504, 798, 540, 20, 38, 513, 148]
여섯 살 적에 나는 "체험한 이야기"라는 제목의, 원시림에 관한 책에서 기막힌 그림 하나를


### One-hot representations
We can use ***NDArray’s one_hot() operation*** to render a one-hot representation of each character. But frack it, since this is the from scratch tutorial, let’s write this ourselves.



In [0]:
# text --> one-hot
def one_hots(numerical_list, vocab_size=vocab_size):
  result = nd.zeros((len(numerical_list), vocab_size), ctx=ctx)
  for i, idx in enumerate(numerical_list):
    result[i, idx] = 1.0
  return result

In [32]:
prince_numerical[:2]

[114, 679]

In [33]:
print(one_hots(prince_numerical[:2]))


[[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]
<NDArray 2x850 @gpu(0)>


In [0]:
# one-hot --> text
def textify(embedding):
  result = ""
  indices = nd.argmax(embedding, axis=1).asnumpy()
  for idx in indices:
    result += character_list[int(idx)]
  return result

In [35]:
textify(one_hots(prince_numerical[:40]))

'여섯 살 적에 나는 "체험한 이야기"라는 제목의, 원시림에 관한 책에서 '

### Preparing the data for training

In [36]:
len(prince_numerical)

45772

In [37]:
((len(prince_numerical)-1) // 64) * 64
# time_numerical[]

45760

In [38]:
%%time

## make sequence (64길이 단위로 자름)
seq_length = 64

# -1 here so we have enough characters for labels later
num_samples = (len(prince_numerical)-1) // seq_length
dataset = one_hots(prince_numerical[:seq_length*num_samples]).reshape((num_samples, seq_length, vocab_size)) # (시퀀스갯수 * 시퀀스길이 * 임베딩)
print(dataset[0] , '\n' , textify(dataset[0]))


[[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]
<NDArray 64x850 @gpu(0)> 
 여섯 살 적에 나는 "체험한 이야기"라는 제목의, 원시림에 관한 책에서 기막힌 그림 하나를 본 적이 있다. 맹수를 
CPU times: user 6.3 s, sys: 1.04 s, total: 7.34 s
Wall time: 4.69 s


#### Preparing input batch 

In [39]:
dataset.shape # (시퀀스갯수 * 시퀀스길이 * 임베딩)

(715, 64, 850)

In [0]:
# batch size 지정
batch_size = 32

In [41]:
print('# of sequences in dataset: ', len(dataset))
num_batches = len(dataset) // batch_size
print('# of batches: ', num_batches)
train_data = dataset[:num_batches*batch_size].reshape((batch_size, num_batches, seq_length, vocab_size)) #(batch_size, num_batches, seq_length, vocab_size)


# of sequences in dataset:  715
# of batches:  22


In [42]:
train_data.shape #(batch_size, num_batches, seq_length, vocab_size)

(32, 22, 64, 850)

In [43]:
# (축을 바꿔줌) swap batch_size and seq_length axis to make later access easier
train_data = nd.swapaxes(train_data, 0, 1)
train_data = nd.swapaxes(train_data, 1, 2)
print('Shape of data set:' , train_data.shape) # (num_batches, seq_length, batch_size, vocab_size)

Shape of data set: (22, 64, 32, 850)


In [44]:
for i in range(3):
    print("***Batch %s:***\n %s \n %s \n %s \n\n" % (i, textify(train_data[i, :, 0]), textify(train_data[i, :, 1]), textify(train_data[i, :, 2])))


***Batch 0:***
 여섯 살 적에 나는 "체험한 이야기"라는 제목의, 원시림에 관한 책에서 기막힌 그림 하나를 본 적이 있다. 맹수를  
 군데 부서져 버린 것이다.기사도 승객도 없었으므로나는 혼자서 어려운 수선을 시도해 보려는 채비를 갖추었다. 그것은  
 다. 그래서 나는 양을 그렸다.  그는 주의 깊게 바라보더니,  "안돼! 그 양은 벌써 병이 들었는 걸"하고 말했다 


***Batch 1:***
 집어삼키고 있는 보아 구렁이 그림이었다. 위의 그림은 그것을 옮겨 그린 것이다.  그 책에는 이렇게 씌어 있었다.  
 나에게는 죽느냐 사느냐의 문제였다. 이렛날 동안 마실 수 있는물밖에 남아 있지 않았다.  첫날밤 나는 사람 사는 고 
 .  "다시 하나 그려 줘."  나는 또 그렸다.  내 친구는 너그러운 모습으로 상냥한 미소를 지었다.  "봐... 


***Batch 2:***
  "보아 구렁이는 먹이를 씹지도 않고 통째로 집어삼킨다.그리고는 꼼짝도 하지 못하고 여섯 달 동안 잠을 자면서 그것 
 장에서 수천 마일 떨어진 사막에서 잠이 들었다.대양 한가운데에 떠 있는 뗏목 위의 표류자보다나는 더 고립되어 있었다 
 ... 이건 양이 아니라 염소잖아. 뿔이 있으니까......"  그래서 난 또다시 그렸다.그러나 그것도 앞의 것들과 




#### Preparing our labels

In [45]:
labels = one_hots(prince_numerical[1:seq_length*num_samples+1]) # 한 글자씩 밀린 캐릭터 리스트를 one hot encoding
train_label = labels.reshape((batch_size, num_batches, seq_length, vocab_size))
train_label = nd.swapaxes(train_label, 0, 1)
train_label = nd.swapaxes(train_label, 1, 2)
print(train_label.shape) # input batch와 같은 shape으로 맞춰줌 


(22, 64, 32, 850)


### A Final Sanity Check
Remember that our target at every time step is to predict the next character in the sequence. So our labels should look just like our inputs but offset by one character. Let’s look at corresponding inputs and outputs to make sure everything lined up as expected.

In [46]:
# input and label이 제대로 페어링 되었는지 확인
print(textify(train_data[10, :, 3]))
print(textify(train_label[10, :, 3]))


소혹성(小惑星) 3251호" 라는 식으로 부르는 것이다.  나는 어린 왕자가 살던 별이소혹성 B612호라고 믿을 만
혹성(小惑星) 3251호" 라는 식으로 부르는 것이다.  나는 어린 왕자가 살던 별이소혹성 B612호라고 믿을 만한


## Recurrent neural networks

Recall that the update for an ordinary hidden layer in a neural network with activation function ϕ is given by

*  ***h=ϕ(xW+b)***

in RNN, need to add a weight sum of the previous hidden state h(t-1)
*  ***h(t)=ϕ( x(t)W(xh)+h(t−1)W(hh)+b(h) )***

Then at every time step t, we'll calculate the output as:
* ***y(t)_hat = softmax(h(t)W(hy)+b(y)***


### Allocate parameters

In [0]:
num_inputs = vocab_size # input character dimension
num_hidden = 256 # hidden cell dimension
num_outputs = vocab_size # output character dimension

########################
#  Weights connecting the inputs to the hidden layer (W(xh))
########################
Wxh = nd.random_normal(shape=(num_inputs,num_hidden), ctx=ctx) * .01 ## 0.01을 곱하는 의미가 뭐지??

########################
#  Recurrent weights connecting the hidden layer across time steps
########################
Whh = nd.random_normal(shape=(num_hidden,num_hidden), ctx=ctx) * .01

########################
#  Bias vector for hidden layer
########################
bh = nd.random_normal(shape=num_hidden, ctx=ctx) * .01


########################
# Weights to the output nodes
########################
Why = nd.random_normal(shape=(num_hidden,num_outputs), ctx=ctx) * .01
by = nd.random_normal(shape=num_outputs, ctx=ctx) * .01

# NOTE: to keep notation consistent,
# we should really use capital letters
# for hidden layers and outputs,
# since we are doing batchwise computations]

### Attach the gradients

In [0]:
params = [Wxh, Whh, bh, Why, by]
for param in params:
  param.attach_grad()

### Softmax Activation

In [0]:
def softmax(y_linear, temperature=1.0):
  lin = (y_linear-(nd.max(y_linear, axis=1).reshape((-1,1)))) / temperature
  exp = nd.exp(lin)
  partition = nd.sum(exp, axis=1).reshape((-1,1))
  return exp / partition

In [50]:
####################
# With a temperature of 1 (always 1 during training), we get back some set of probabilities
####################
softmax(nd.array([[1, -1], [-1, 1]]), temperature=1.0)



[[0.880797   0.11920292]
 [0.11920292 0.880797  ]]
<NDArray 2x2 @cpu(0)>

In [51]:
####################
# Often we want to sample with low temperatures to produce sharp probabilities
####################
softmax(nd.array([[10,-10],[-10,10]]), temperature=0.1)



[[1. 0.]
 [0. 1.]]
<NDArray 2x2 @cpu(0)>

In [52]:
####################
# If we set a high temperature, we can get more entropic (*noisier*) probabilities
####################
softmax(nd.array([[1,-1],[-1,1]]), temperature=1000.0)



[[0.50049996 0.49949998]
 [0.49949998 0.50049996]]
<NDArray 2x2 @cpu(0)>

### Define the model

In [0]:
def simple_rnn(inputs, state, temperature=1.0):
  outputs = []
  h = state
  for X in inputs:
    h_linear = nd.dot(X, Wxh) + nd.dot(h, Whh) + bh
    h = nd.tanh(h_linear)
    yhat_linear = nd.dot(h, Why) + by
    yhat = softmax(yhat_linear, temperature = temperature)
    outputs.append(yhat)
  return(outputs, h)

### Cross-entropy loss function

In [0]:
# def cross_entropy(yhat, y):
#     return - nd.sum(y * nd.log(yhat))

def cross_entropy(yhat, y):
    return - nd.mean(nd.sum(y * nd.log(yhat), axis=0, exclude=True))

In [55]:
cross_entropy(nd.array([[.2,.5,.3], [.2,.5,.3]]), nd.array([[1.,0,0], [0, 1.,0]]))



[1.1512926]
<NDArray 1 @cpu(0)>

### Averaging the loss over the sequence
Because the unfolded RNN has multiple outputs (one at every time step) we can calculate a loss at every time step. The weights corresponding to the net at time step t influence both the loss at time step t and the loss at time step t+1. To combine our losses into a single global loss, we’ll take the average of the losses at each time step.

In [0]:
def average_ce_loss(outputs, labels):
  assert(len(outputs) == len(labels))
  total_loss = 0
  for(output, label) in zip(outputs, labels):
    total_loss = total_loss + cross_entropy(output,label)
  return total_loss / len(outputs)
  

### Optimizer

In [0]:
def SGD(params, lr):
  for param in params:
    param[:] = param - lr * param.grad

## Generating text by sampling

We have now defined a model that takes a sequence of real inputs from our training data and tries to predict the next character at every time step. You might wonder, what can we do with this model? Why should I care about predicting the next character in a sequence of text?

This capability is exciting because given such a model, we can now generate strings of plausible text. The generation procedure goes as follows. 


---

Say our string begins with the character “T”. We can feed the letter “T” and get a conditional probability distribution over the next character P(x2|x1="T"). We can the sample from this distribution, e.g. producing an “i”, and then assign x2="i", feeding this to the network at the next time step.



In [0]:
def sample(prefix, num_chars, temperature=1.0):
    #####################################
    # Initialize the string that we'll return to the supplied prefix
    #####################################
    string = prefix

    #####################################
    # Prepare the prefix as a sequence of one-hots for ingestion by RNN
    #####################################
    prefix_numerical = [character_dict[char] for char in prefix]
    input_sequence = one_hots(prefix_numerical)

    #####################################
    # Set the initial state of the hidden representation ($h_0$) to the zero vector
    #####################################
    sample_state = nd.zeros(shape=(1, num_hidden), ctx=ctx)

    #####################################
    # For num_chars iterations,
    #     1) feed in the current input
    #     2) sample next character from from output distribution
    #     3) add sampled character to the decoded string
    #     4) prepare the sampled character as a one_hot (to be the next input)
    #####################################
    for i in range(num_chars):
        outputs, sample_state = simple_rnn(input_sequence, sample_state, temperature=temperature)
        choice = np.random.choice(vocab_size, p=outputs[-1][0].asnumpy())
        string += character_list[choice]
        input_sequence = one_hots([choice])
    return string

In [59]:
%%time

epochs = 2000
moving_loss = 0.

learning_rate = .5

# state = nd.zeros(shape=(batch_size, num_hidden), ctx=ctx)
for e in range(epochs):
    ############################
    # Attenuate the learning rate by a factor of 2 every 100 epochs.
    ############################
    if ((e+1) % 100 == 0):
        learning_rate = learning_rate / 2.0
    state = nd.zeros(shape=(batch_size, num_hidden), ctx=ctx)
    for i in range(num_batches):
        data_one_hot = train_data[i]
        label_one_hot = train_label[i]
        with autograd.record():
            outputs, state = simple_rnn(data_one_hot, state)
            loss = average_ce_loss(outputs, label_one_hot)
            loss.backward()
        SGD(params, learning_rate)

        ##########################
        #  Keep a moving average of the losses
        ##########################
        if (i == 0) and (e == 0):
            moving_loss = np.mean(loss.asnumpy()[0])
        else:
            moving_loss = .99 * moving_loss + .01 * np.mean(loss.asnumpy()[0])

    print("Epoch %s. Loss: %s" % (e, moving_loss))
    print(sample("어린 왕자", 1024, temperature=.1))
    print(sample("나는 지구가 좋아.", 1024, temperature=.1))


Epoch 0. Loss: 6.763629183029039
어린 왕자                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  

In [0]:
file_name = "net.params"
